In [37]:
import numpy as np
import tensorflow as tf
import pandas as pd

In [38]:
train = pd.read_csv('/users/nikki/Downloads/all (1)/train.csv')
test = pd.read_csv('/users/nikki/Downloads/all (1)/test.csv')

In [39]:
target = train["label"]
# Drop 'label' column
X_train = train.drop(labels = ["label"],axis = 1) 

# free some space
del train 

In [40]:
#Create a train/test set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X_train,target, test_size=0.2, random_state=42)
y_train = np.asarray(y_train, dtype=np.int32)
y_test  =np.asarray(y_test, dtype=np.int32)
batch_size =len(X_train)
print(X_train.shape, y_train.shape,y_test.shape, test.shape )


(33600, 784) (33600,) (8400,) (28000, 784)


In [43]:
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()
# Train
X_train_scaled = scaler.fit_transform(X_train.astype(np.float32))
X_train_scaled = X_train_scaled.astype(np.float32)
# test
X_test_scaled = scaler.fit_transform(X_test.astype(np.float32))
X_test_scaled = X_test_scaled.astype(np.float32)

test_scaled = scaler.fit_transform(test.astype(np.float32))
test_scaled = test_scaled.astype(np.float32)


feature_columns = [tf.feature_column.numeric_column('x', shape=X_train_scaled.shape[1:])]
X_train_scaled.shape[1:]
print(X_train_scaled.dtype)
print(test_scaled.dtype)

/usr/local/lib/python3.7/site-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype float32 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)
/usr/local/lib/python3.7/site-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype float32 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)
/usr/local/lib/python3.7/site-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype float32 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)


float32
float32


In [6]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [7]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x1163e2048>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [8]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
    tensors=tensors_to_log, every_n_iter=50)

In [9]:
# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": X_train_scaled},
    y=y_train,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.10247858 0.10591222 0.09500289 0.09619953 0.10731108 0.09450483
  0.10261524 0.09277703 0.10630205 0.09689653]
 [0.09765597 0.1131788  0.08928759 0.10157288 0.10622763 0.09514891
  0.10072476 0.09642567 0.11495364 0.08482413]
 [0.11015504 0.09651745 0.08255797 0.10938286 0.11335985 0.09282816
  0.09281934 0.0915354  0.11401948 0.09682446]
 [0.10488161 0.10702011 0.08546425 0.10063503 0.10470032 0.09354322
  0.09816345 0.09948879 0.11092554 0.09517764]
 [0.10901566 0.11268515 0.08461411 0.10384889 0.11642601 0.08730016
  0.09933493 0.08453813 0.10391089 0.09832609]
 [0.12009662 0.098777   0.0891421  0.10521948 0.1000976  0.0925679
  0.10275684 0.10039189 0.10251611 0.08843445]
 [0.09619827 0.10546292 0.09188884 0.08860267 0.10818925 0.10701625
  0.09719995 0.09835996 0.10144005 0.1056419 ]
 [0.1097054  0.10388441 0.09341834 0.

INFO:tensorflow:loss = 2.3101532, step = 1
INFO:tensorflow:probabilities = [[0.0917347  0.0989182  0.08919307 0.10651044 0.10471356 0.10642987
  0.10301532 0.10219442 0.10574018 0.09155023]
 [0.10654153 0.10653284 0.10094786 0.09231171 0.10367943 0.09900403
  0.10289634 0.09480548 0.09850244 0.09477834]
 [0.10045751 0.10551585 0.08607043 0.11189628 0.10393748 0.10975279
  0.10038792 0.08516644 0.10648175 0.09033354]
 [0.09818138 0.10993687 0.08633909 0.09058218 0.11178316 0.09402017
  0.09586902 0.10205593 0.1080161  0.10321617]
 [0.09986618 0.0992395  0.09543735 0.09946464 0.10535121 0.09649714
  0.1057952  0.0906248  0.10874148 0.09898248]
 [0.10426028 0.09988965 0.09405516 0.0940863  0.10338404 0.09150409
  0.10559291 0.10010568 0.10295033 0.10417145]
 [0.09927755 0.10233273 0.09304758 0.09311409 0.11061698 0.10345595
  0.10750052 0.09545804 0.09706976 0.09812675]
 [0.10608499 0.0999862  0.09709264 0.09899334 0.10995413 0.10257135
  0.10068254 0.08709659 0.10802168 0.08951652]
 [0.1

INFO:tensorflow:global_step/sec: 3.94584
INFO:tensorflow:probabilities = [[0.09246623 0.10595053 0.09172384 0.10229362 0.11868192 0.08217657
  0.10646865 0.09514946 0.1093076  0.09578166]
 [0.10995203 0.0990495  0.09367125 0.09325501 0.11132335 0.0961037
  0.10818291 0.09317721 0.10642545 0.08885959]
 [0.09916215 0.09611058 0.09741388 0.09960701 0.11253407 0.09091698
  0.11022069 0.09296059 0.10227779 0.09879635]
 [0.1037465  0.10060719 0.08575783 0.10219639 0.10399528 0.09572751
  0.10368406 0.10933498 0.09349819 0.10145208]
 [0.10475536 0.09913545 0.1012888  0.10965246 0.10461244 0.09124993
  0.10398349 0.09399668 0.09739714 0.09392829]
 [0.10470974 0.10072279 0.08894456 0.1020872  0.10586338 0.09306176
  0.10249343 0.09655447 0.11057631 0.0949863 ]
 [0.11026359 0.09403839 0.09731122 0.09968896 0.12083356 0.08800309
  0.0929058  0.09426825 0.11283303 0.0898541 ]
 [0.10676219 0.10493805 0.09441543 0.09581111 0.11189552 0.09178557
  0.09617979 0.10086176 0.10226487 0.09508571]
 [0.1081

INFO:tensorflow:loss = 2.3102427, step = 101 (25.344 sec)
INFO:tensorflow:probabilities = [[0.10709979 0.09622152 0.09363282 0.10564961 0.10980228 0.0990809
  0.09632057 0.09077784 0.10683874 0.09457599]
 [0.10600908 0.10180791 0.0956388  0.09555965 0.10713939 0.09088828
  0.09998333 0.09775858 0.10804501 0.09716999]
 [0.09996974 0.10039039 0.09561273 0.09898661 0.10692991 0.08880834
  0.0947672  0.09566496 0.11373948 0.10513058]
 [0.0963246  0.10122246 0.09304373 0.10275501 0.10837725 0.09780674
  0.09113479 0.10717848 0.10409921 0.09805771]
 [0.10474845 0.09635739 0.09588915 0.09528246 0.1093835  0.09424514
  0.10344503 0.0887313  0.11132682 0.10059072]
 [0.11463697 0.09252146 0.08517557 0.10182798 0.11462133 0.08432245
  0.10787117 0.09568568 0.11382734 0.08951002]
 [0.10324271 0.10053213 0.09214744 0.09695537 0.09954807 0.09834437
  0.10982074 0.09732541 0.10565421 0.09642956]
 [0.09983691 0.11035616 0.09209663 0.09471858 0.10523717 0.09505581
  0.09990676 0.09916706 0.1014395  0.1

INFO:tensorflow:global_step/sec: 3.98832
INFO:tensorflow:probabilities = [[0.10561173 0.10830002 0.08442129 0.09842141 0.10325195 0.09887826
  0.09914438 0.10225087 0.10683518 0.09288491]
 [0.10245422 0.11675683 0.08530388 0.10611998 0.10905062 0.0973298
  0.09626787 0.08586302 0.10462269 0.09623115]
 [0.1077252  0.10013595 0.09208753 0.0888475  0.11175726 0.10681823
  0.09867798 0.10050946 0.09431446 0.09912635]
 [0.10399648 0.09367651 0.08192459 0.10177852 0.10117648 0.09324011
  0.11171056 0.09594005 0.11591805 0.10063867]
 [0.10519372 0.09720619 0.10637653 0.10454363 0.11019172 0.10315798
  0.10177959 0.07819402 0.10454325 0.08881333]
 [0.10175738 0.10230199 0.09989917 0.10396656 0.10486141 0.08785991
  0.10485297 0.09264857 0.10699443 0.09485753]
 [0.10742249 0.08672769 0.09656005 0.10315035 0.10881471 0.10519849
  0.0988989  0.09155178 0.10360212 0.09807338]
 [0.10544752 0.10262506 0.08295491 0.09219921 0.10686932 0.10144506
  0.09906103 0.09563486 0.10908166 0.10468134]
 [0.1025

...

INFO:tensorflow:global_step/sec: 3.53638
INFO:tensorflow:probabilities = [[0.00006784 0.99685943 0.00017703 0.00004069 0.00005477 0.00010712
  0.00072634 0.00029167 0.00163692 0.00003822]
 [0.9997043  0.00000008 0.00003683 0.0000092  0.00000002 0.00005688
  0.00000136 0.00004353 0.00000037 0.00014751]
 [0.00000188 0.0000272  0.00000843 0.00091853 0.85195017 0.01727304
  0.00012152 0.01452775 0.00073916 0.11443226]
 [0.00003041 0.00000607 0.9956892  0.00007038 0.00144622 0.00001443
  0.00008702 0.00238023 0.00002224 0.00025382]
 [0.00079654 0.01597144 0.06852765 0.00571176 0.71202123 0.00500684
  0.03477431 0.01996394 0.10436342 0.03286283]
 [0.03774872 0.00105462 0.00107977 0.00073163 0.00124449 0.94794166
  0.00454251 0.00172637 0.00374697 0.00018321]
 [0.00000487 0.00000046 0.00006109 0.00000005 0.00006929 0.00032937
  0.9995165  0.         0.00001805 0.00000029]
 [0.00003897 0.00023494 0.00100097 0.00080928 0.02299045 0.00022858
  0.00003903 0.00961551 0.00114843 0.96389383]
 [0.000

INFO:tensorflow:loss = 0.054446395, step = 19801 (28.280 sec)
INFO:tensorflow:probabilities = [[0.         0.00000059 0.00000729 0.00003211 0.00000024 0.00000019
  0.         0.999913   0.00000012 0.00004654]
 [0.99995327 0.         0.00000077 0.         0.         0.00003905
  0.00000045 0.00000002 0.00000635 0.00000006]
 [0.0000068  0.00000135 0.00011707 0.9982326  0.00000048 0.00081235
  0.00000001 0.00004781 0.00063466 0.00014674]
 [0.00000117 0.00000018 0.00002513 0.         0.00004434 0.00000375
  0.9999243  0.00000002 0.00000107 0.00000001]
 [0.00006233 0.00000024 0.0000004  0.00003379 0.00000185 0.0014428
  0.00000001 0.997097   0.00000039 0.00136129]
 [0.97619265 0.00000299 0.01687337 0.00028334 0.00014228 0.00009354
  0.00001426 0.00132738 0.00025413 0.00481593]
 [0.00000008 0.0000002  0.00000016 0.00013253 0.66892916 0.00010222
  0.00000015 0.00224332 0.00015584 0.32843632]
 [0.00047518 0.00003896 0.00192761 0.00075334 0.00004064 0.00005024
  0.00000006 0.9627124  0.00112316

INFO:tensorflow:global_step/sec: 3.10227
INFO:tensorflow:probabilities = [[0.00011668 0.00084958 0.00102634 0.03150732 0.00132566 0.00499654
  0.0000556  0.00034977 0.9532287  0.00654386]
 [0.00000167 0.0000024  0.00002266 0.00210013 0.00173359 0.00057923
  0.00000017 0.00292691 0.00054665 0.9920866 ]
 [0.00000887 0.00000023 0.00003365 0.00001178 0.00000039 0.00018355
  0.00000811 0.00000004 0.9997515  0.0000019 ]
 [0.         0.         0.00000112 0.0000412  0.00000003 0.00000018
  0.         0.999949   0.00000019 0.00000814]
 [0.00000054 0.00001771 0.00011233 0.9964588  0.00000033 0.00061761
  0.00000083 0.00000016 0.00275938 0.00003235]
 [0.00005218 0.00003259 0.00110395 0.00002341 0.00184539 0.00012247
  0.9960068  0.00000195 0.00079864 0.00001249]
 [0.9997744  0.         0.00001085 0.00000035 0.00000006 0.00000201
  0.00000121 0.00000474 0.00001114 0.00019526]
 [0.00012645 0.8862213  0.00063394 0.0000781  0.0002956  0.00143866
  0.05932679 0.00000806 0.05181532 0.00005581]
 [0.000

INFO:tensorflow:loss = 0.12828079, step = 19901 (32.232 sec)
INFO:tensorflow:probabilities = [[0.00001613 0.00003373 0.99558616 0.00404361 0.00000015 0.00000074
  0.00000417 0.00000541 0.0003079  0.00000198]
 [0.00014175 0.9789802  0.00426615 0.00198725 0.00240665 0.00281688
  0.00397213 0.00183585 0.00323259 0.00036065]
 [0.00020045 0.00000014 0.00000919 0.00020414 0.00000358 0.9987852
  0.0000211  0.0000005  0.0007583  0.00001738]
 [0.0000014  0.00000263 0.00000141 0.0000032  0.00172707 0.00000136
  0.00000002 0.0056571  0.00004297 0.99256283]
 [0.00001968 0.00000139 0.9960306  0.00377454 0.00000555 0.00001042
  0.00006247 0.00000573 0.00008085 0.00000882]
 [0.00000333 0.00008462 0.9994469  0.00036742 0.0000045  0.00000026
  0.00005291 0.00001276 0.0000269  0.00000037]
 [0.9999776  0.         0.00000048 0.00000165 0.         0.00001691
  0.00000177 0.00000128 0.00000008 0.00000026]
 [0.00000499 0.00000117 0.00018495 0.00000005 0.00004508 0.0000472
  0.9996654  0.00000002 0.0000489  0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.1380493.


In [16]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": X_test_scaled},
    y=y_test,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Starting evaluation at 2019-01-22-02:21:05
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2019-01-22-02:21:12
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.96380955, global_step = 20000, loss = 0.11849036
{'accuracy': 0.96380955, 'loss': 0.11849036, 'global_step': 20000}


In [50]:
# Predict the model
pred_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x":test_scaled},
    num_epochs = 1,
    shuffle = False
)
pred_results = mnist_classifier.predict(input_fn = pred_input_fn)

arr = list()
for pred in pred_results:
    arr.append(pred['classes'])
    
predictions = np.array(arr)  
print(predictions)

INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
[2 0 9 ... 3 9 2]


FileNotFoundError: File b'../input/sample_submission.csv' does not exist